<a href="https://colab.research.google.com/github/tprasadtp/jupyter-notebooks/blob/master/dsp/CPU_Python_Convolve.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>


# Convolution


In [1]:
# Deps
! pip install librosa

In [0]:
# Importing Stuff
import math
import numpy as np
import IPython.display as ipd
import numpy as np
from scipy.io import wavfile 
import os
import sys
import warnings

%matplotlib inline
import matplotlib.pyplot as plt
import librosa.display

try:
    from IPython.display import Audio
except:
    warnings.warn("Can't import Audio from IPython.display; "
                  "Wave.audio() will not work.")


# Upload the Files you wish to convolve.
Please change the filenames accordigly in the later sections.
You need **Impulse-Response** and **Audio** files in wav format. Please note that Adobe Audion might add some metadata which cannot be read properly. Don t select to include markers while exporting. Files are **NOT** uploaded to Google Drive. they are on a VM's Filesystem.

- You can upload by using Left pane or Hittong upload button below.

In [0]:
from google.colab import files
# Uploading Files
uploaded = files.upload()

for fn in uploaded.keys():
  print('User uploaded file "{name}" with length {length} bytes'.format(
      name=fn, length=len(uploaded[fn])))

## Deleting Old Files
Did you upload files twice? That can happen!. Delete them using normal shell commands.
just add `!` before the command. `!ls` will give you list of files here.

In [0]:
# For your Info You are running on
print ("------ Running on -------")
!uname -a
!lsb_release -a

# Rename your file / edit code
Rename Your files or edit the code below.

- If you wish to keep original code, rename your impulse response file to `impulse.wav` and audio file to `spirit.wav`. 
- Both **SHOULD** be **STEREO**

-- If you want to edit code, just change the filenames below. `spirit.wav` to  input audio file and `impulse.wav` to name of your impulse response file.

# Read Files

In [3]:
# Read Wav Files
# audio is input, ir is impulse response.

# Read Audio File
# Ignore warnings of chunk data if any.

print("Reading Audio file.....")
samp_rate, audio = wavfile.read("spirit.wav")
print("Reading Impulse response ==> ......|..... ;)")
_ , impulse = wavfile.read("impulse.wav")

Reading Audio file.....
Reading Impulse response ==> ......|..... ;)


/usr/local/lib/python3.6/dist-packages/scipy/io/wavfile.py:273: WavFileWarning: Chunk (non-data) not understood, skipping it.
  WavFileWarning)


In [4]:
audio_rows, audio_cols = np.shape(audio)
if audio_cols == 2:
    print ('Source is Stereo file.')
    audio_l = audio[:,0]
    audio_r = audio[:,1]
    # Lets set a Flag.
    audio_stereo = True
elif audio_cols == 1:
    print('Source is Mono')
    audio_l = audio
    audio_stereo = False
else:
    print('Multi channel Audio is not suppoted')

if audio_rows / samp_rate  < 0.5:
    print('Audio is Too short to play with')
    sys.exit(1)
else:
    print ("Audio is {0:f} seconds long.".format(audio_rows/samp_rate))

## Impulse Stereo
    
impulse_rows, impulse_cols = np.shape(impulse)

if impulse_cols == 2:
    print ('Immpulse is Stereo file.')
    impulse_l = impulse[:,0]
    impulse_r = impulse[:,1]
    # Lets set a Flag.
    impulse_stereo = True
elif audio_cols == 1:
    print('Impulse is Mono')
    impulse_l = audio
    impulse_stereo = False
else:
    print('Multi channel Audio is not suppoted')


Source is Stereo file.
Audio is 21.090476 seconds long.
Immpulse is Stereo file.


# Processing Channels

- Normalize the audio samples b/w 1 & -1
- fft shift both channels
- fftshift impulse
- convolve
- inverse FFT
- Make audio

In [5]:
# Define normalize func 
def normalize(ys, amp=1.0):
    """Normalizes a wave array so the maximum amplitude is +amp or -amp.

    ys: wave array
    amp: max amplitude (pos or neg) in result

    returns: wave array
    """
    high, low = abs(max(ys)), abs(min(ys))
    return amp * ys / max(high, low)


print("Normalizing Numpy Arrays....")
# Normalize 
if (not impulse_stereo) and (not audio_stereo):
    print("Both Impulse and Audio are Mono")
    audio_l_n = normalize(audio_l)
    impulse_l_n = normalize(impulse_l)
    # Set a global flag easier on if next time
    STEREO = False
elif impulse_stereo and audio_stereo:
    print("Both Impulse and Audio are Stereo")
    audio_l_n = normalize(audio_l)
    impulse_l_n = normalize(impulse_l)
    audio_r_n = normalize(audio_r)
    impulse_r_n = normalize(impulse_r)
    STEREO = True
else:
    print("Channel mismatch!. Wither Both should be Mono or both should be Stereo!")
    sys.exit(1)
    
## FFT Shift
print("FFT Shift...")
print("Processing Left(or Mono) channel...")
audio_l_n_fft = np.fft.fftshift(audio_l_n)
impulse_l_n_fft = np.fft.fftshift(impulse_l_n)

if STEREO:
    print ("FFTShift Right Channels...")
    audio_r_n_fft = np.fft.fftshift(audio_r_n)
    impulse_r_n_fft = np.fft.fftshift(impulse_r_n)

# Convolve

print ("Convolve Channels seperately ....")
print("Processing Left(or Mono) channel...")
audio_l_fft_convolve = np.convolve(audio_l_n_fft, impulse_l_n_fft, mode="full")
audio_l_convolve = np.fft.ifftshift(audio_l_fft_convolve)

if STEREO:
    print("Convolving Right Channel.....")
    audio_r_fft_convolve = np.convolve(audio_r_n_fft, impulse_r_n_fft, mode="full")
    audio_r_convolve = np.fft.ifftshift(audio_r_fft_convolve)


# Renormalize
print("Renormalizing Outputs...")
print("Processing Left(or Mono) channel...")
audio_l_convolve_n = normalize(audio_l_convolve)
if STEREO:
    print("Processing Right Channel....")
    audio_r_convolve_n = normalize(audio_r_convolve)



    

Normalizing Numpy Arrays....
Both Impulse and Audio are Stereo
FFT Shift...
Processing Left(or Mono) channel...
FFTShift Right Channels...
Convolve Channels seperately ....
Processing Left(or Mono) channel...
Convolving Right Channel.....
Renormalizing Outputs...
Processing Left(or Mono) channel...
Processing Right Channel....


In [9]:

wavfile.write("convolved_left.wav", samp_rate, audio_l_convolve_n)
ipd.Audio(audio_l_convolve_n, rate=samp_rate)

# Center Channel Removal (Invert One Channel)

Invert a Channel and add it to other.

In [12]:
# Remove Center Channel
print("Center Channel Removal (Simple)")
if audio_stereo:
    print("Processing Audio")
    audio_center = audio_l_n - audio_r_n
    wavfile.write("center_channel.wav", samp_rate, audio_center)
else:
    print("Audio is not Stereo...")
    
ipd.Audio(audio_center, rate=samp_rate)

Center Channel Removal (Simple)
Processing Audio
